In [3]:
import re

In [4]:
import contractions

In [5]:
from nltk.corpus import stopwords

In [6]:
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer

In [7]:
from sklearn.naive_bayes import MultinomialNB

In [8]:
from sklearn.model_selection import train_test_split

In [9]:
from scipy.sparse import hstack, csr_matrix

In [10]:
from sklearn.metrics import accuracy_score, recall_score, f1_score

In [11]:
from sklearn.model_selection import KFold, cross_val_score, GridSearchCV

In [12]:
from sklearn.pipeline import Pipeline

In [13]:
from transformers import pipeline

D:\Program Files\Anaconda\Lib\site-packages\transformers\utils\generic.py:260: FutureWarning: `torch.utils._pytree._register_pytree_node` is deprecated. Please use `torch.utils._pytree.register_pytree_node` instead.
  torch.utils._pytree._register_pytree_node(


In [14]:
blogs = pd.read_csv('blogs.csv')
blogs

<IPython.core.display.Javascript object>

Data              Labels
0     Path: cantaloupe.srv.cs.cmu.edu!magnesium.club...         alt.atheism
1     Newsgroups: alt.atheism\nPath: cantaloupe.srv....         alt.atheism
2     Path: cantaloupe.srv.cs.cmu.edu!das-news.harva...         alt.atheism
3     Path: cantaloupe.srv.cs.cmu.edu!magnesium.club...         alt.atheism
4     Xref: cantaloupe.srv.cs.cmu.edu alt.atheism:53...         alt.atheism
...                                                 ...                 ...
1995  Xref: cantaloupe.srv.cs.cmu.edu talk.abortion:...  talk.religion.misc
1996  Xref: cantaloupe.srv.cs.cmu.edu talk.religion....  talk.religion.misc
1997  Xref: cantaloupe.srv.cs.cmu.edu talk.origins:4...  talk.religion.misc
1998  Xref: cantaloupe.srv.cs.cmu.edu talk.religion....  talk.religion.misc
1999  Xref: cantaloupe.srv.cs.cmu.edu sci.skeptic:43...  talk.religion.misc

[2000 rows x 2 columns]

In [225]:
#Getting all the categories of blogs
categories = blogs['Labels'].unique()
no_of_categories = blogs['Labels'].nunique()
print('Categores:')
print(categories)
print('No. of Categories:',no_of_categories)

Categores:
['alt.atheism' 'comp.graphics' 'comp.os.ms-windows.misc'
 'comp.sys.ibm.pc.hardware' 'comp.sys.mac.hardware' 'comp.windows.x'
 'misc.forsale' 'rec.autos' 'rec.motorcycles' 'rec.sport.baseball'
 'rec.sport.hockey' 'sci.crypt' 'sci.electronics' 'sci.med' 'sci.space'
 'soc.religion.christian' 'talk.politics.guns' 'talk.politics.mideast'
 'talk.politics.misc' 'talk.religion.misc']
No. of Categories: 20


### There are 20 different categories of blogs

In [226]:
#Getting the no. of blogs in each category
blogs['Labels'].value_counts()

Labels
alt.atheism                 100
comp.graphics               100
talk.politics.misc          100
talk.politics.mideast       100
talk.politics.guns          100
soc.religion.christian      100
sci.space                   100
sci.med                     100
sci.electronics             100
sci.crypt                   100
rec.sport.hockey            100
rec.sport.baseball          100
rec.motorcycles             100
rec.autos                   100
misc.forsale                100
comp.windows.x              100
comp.sys.mac.hardware       100
comp.sys.ibm.pc.hardware    100
comp.os.ms-windows.misc     100
talk.religion.misc          100
Name: count, dtype: int64

### There are 100 blogs in each category

In [15]:
#Function to save the 'subject' metadata
def save_subject(text):
    match = re.search(r'Subject:\s*(Re:\s*)?(.*)\s*\n', text)
    if match:
        return match.group(2)
    else :
        return 'no subject'

# Creating a new dataframe 'data' for blog subjects

In [16]:
data = blogs['Data'].apply(save_subject).to_frame(name='subject')


In [17]:
data.head()

subject
0                    islamic genocide
1                       Not the Omni!
2  Yet more Rushdie [Re: ISLAMIC LAW]
3     Death Penalty / Gulf War (long)
4         Rawlins debunks creationism

# Creating function that comprises text cleaning operations
## remove Metadata, non-alphabetical characters, some unwanted sentences and phrases from the text

In [18]:
#Function to remove Metadata, non-alphabetical characters, some unwanted sentences and phrases from the text
def clean_text(text):
    # Remove lines starting with common metadata patterns like 'Path:', 'Newsgroups:', etc.
    cleaned_text = re.sub(r'''(?m)^(Path|Newsgroups|Xref|From|Subject|Lines|X-Newsreader|Message-ID|Date|
    |Organization|Distribution|References|NNTP-Posting-Host|Nntp-Posting-Host|Sender|Keywords|Reply-To):.*\n?''', '', text)
    
    
    cleaned_text = re.sub(r'\n.*@.*wrote', '', cleaned_text)
    cleaned_text = re.sub(r'In article.*\n', '', cleaned_text)
    cleaned_text = re.sub(r'\s.*writes', '', cleaned_text)
    
    cleaned_text = cleaned_text.lower() #converting entire text to lowercase
    cleaned_text = contractions.fix(cleaned_text) #removing contractions
    
    cleaned_text = re.sub(pattern=r'[^a-zA-Z0-9\s]', repl=' ', string=cleaned_text)#removing non-alphanumeric characters
    cleaned_text = re.sub(r'\b\d+\b', '', cleaned_text) #removing standalone numerical digits
    cleaned_text = re.sub(r'\b\S*\d\S*\b', '', cleaned_text)#removing all words that contain digits
    cleaned_text = re.sub(r'\s+', ' ', cleaned_text).strip()


    return cleaned_text

In [19]:
# Add the clean blog text to 'data'
data['text'] = blogs['Data'].apply(clean_text)

In [20]:
# Apply the text cleaning operation on subject as well
data['subject'] = data['subject'].apply(clean_text)

In [21]:
data.head()

subject  \
0                 islamic genocide   
1                     not the omni   
2  yet more rushdie re islamic law   
3      death penalty gulf war long   
4      rawlins debunks creationism   

                                                text  
0  noting that a particular society in this case ...  
1  please enlighten me how is omnipotence contrad...  
2  p s i am not sure about this but i think the c...  
3  which liberal news media are we talking about ...  
4  evolution as i have said before is theory and ...

# Now remove stop words from out text documents

In [264]:
# Fetching the list of stop words
stop_words = set(stopwords.words("english"))
print(stop_words)

{'no', 've', "should've", 'did', 'own', "hasn't", 'it', 'you', 'here', 'why', "she's", 'what', 'i', 'mightn', 'very', 'not', 'him', 'or', 'on', 'yourselves', 'being', 'herself', "shouldn't", 'hers', 'its', 'now', 'to', 'were', 'm', 'under', 'hasn', 'who', "wouldn't", 'both', 'them', 'their', 'which', 'for', 'ourselves', "you'll", 'any', 'off', 'shouldn', 'because', 'through', 'has', 'all', 'nor', 'and', "you've", 'as', 'wouldn', 'there', 'shan', 'don', 'her', 'she', 'how', "didn't", "isn't", 'didn', 'in', 's', 'hadn', "weren't", 'too', 'above', 'over', 'such', 'should', 'down', 'am', 'further', 't', 'then', "shan't", 'we', "it's", 'will', 'with', "wasn't", 'haven', 'yours', 'of', 'that', 'up', 'is', 'during', 'ain', 'me', 'between', "needn't", 'other', 'after', 'out', 'once', 'below', 'only', 'couldn', "mustn't", 'same', 'ma', "couldn't", 'needn', 'be', "that'll", 'had', "doesn't", 'where', 'mustn', 'been', 'yourself', 'but', "don't", "aren't", 'few', 'can', 'themselves', 'this', 'most

In [20]:
list_of_subject_tokens = []
for text in data['subject']:
    text_tokens = [word for word in text.split() if word not in stop_words] #removing the stops words from each subject and storing the remaining words as tokens in a list.
    list_of_subject_tokens.append(text_tokens) 
    
subject = pd.Series(list_of_subject_tokens)#Adding these token_list to a series

<IPython.core.display.Javascript object>

In [21]:
subject.head()

0                  [islamic, genocide]
1                               [omni]
2         [yet, rushdie, islamic, law]
3    [death, penalty, gulf, war, long]
4      [rawlins, debunks, creationism]
dtype: object

In [22]:
list_of_text_tokens = []
for text in data['text']:
    text_tokens = [word for word in text.split() if word not in stop_words] #removing the stops words from each text instance and storing the remaining words as tokens in a list
    list_of_text_tokens.append(text_tokens) 

text = pd.Series(list_of_text_tokens) #Adding these token_list to a series

<IPython.core.display.Javascript object>

In [23]:
text.head()

0    [noting, particular, society, case, mainland, ...
1    [please, enlighten, omnipotence, contradictory...
2    [p, sure, think, charge, shatim, also, applies...
3    [liberal, news, media, talking, western, news,...
4    [evolution, said, theory, fact, exactly, amoun...
dtype: object

In [24]:
#Joining the word tokens back to a single string
subject = subject.apply(lambda x: " ".join(x))
subject

0                   islamic genocide
1                               omni
2            yet rushdie islamic law
3        death penalty gulf war long
4        rawlins debunks creationism
                    ...             
1995    years say christian morality
1996               next mormons jews
1997    gospels josephus etc origins
1998               catholic lit crit
1999               next mormons jews
Length: 2000, dtype: object

In [25]:
#Joining the word tokens back to a single string
text = text.apply(lambda x: " ".join(x))
text

0       noting particular society case mainland uk rel...
1       please enlighten omnipotence contradictory def...
2       p sure think charge shatim also applies rushdi...
3       liberal news media talking western news genera...
4       evolution said theory fact exactly amount exis...
                              ...                        
1995    presumably means moral systems better others m...
1996    fbi claims basis intelligence reports bd plans...
1997    agree creation taught science macroevolution t...
1998    followup talk religion misc alt sex stories al...
1999    followup sci skeptic talk politics misc talk r...
Length: 2000, dtype: object

## Concatenating the text and subject into one string

In [52]:
concatenated_sub_text = subject.str.cat(text, sep=' ')
concatenated_sub_text

0       islamic genocide noting particular society cas...
1       omni please enlighten omnipotence contradictor...
2       yet rushdie islamic law p sure think charge sh...
3       death penalty gulf war long liberal news media...
4       rawlins debunks creationism evolution said the...
                              ...                        
1995    years say christian morality presumably means ...
1996    next mormons jews fbi claims basis intelligenc...
1997    gospels josephus etc origins agree creation ta...
1998    catholic lit crit followup talk religion misc ...
1999    next mormons jews followup sci skeptic talk po...
Length: 2000, dtype: object

## Vectorization using TFIDF

## Vectorizing Subject

In [26]:
tfidf_vectorizer = TfidfVectorizer()
subject_vectors = tfidf_vectorizer.fit_transform(subject)


In [27]:
print("Subject Vectors:\n",subject_vectors.toarray())
print("Tokens:\n", tfidf_vectorizer.get_feature_names_out())
print('No. Of tokens: ', len(tfidf_vectorizer.get_feature_names_out()))

Subject Vectors:
 [[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]
Tokens:
 ['aargh' 'abc' 'abolish' ... 'zionist' 'zone' 'zyxel']
No. Of tokens:  2971


## Vectorizing the blog text

In [28]:
text_vectors = tfidf_vectorizer.fit_transform(text)

In [29]:
print('Text Vectors:\n',text_vectors.toarray())
print('Tokens:', tfidf_vectorizer.get_feature_names_out())
print('No. Of tokens: ', len(tfidf_vectorizer.get_feature_names_out()))

Text Vectors:
 [[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]
Tokens: ['aa' 'aaa' 'aaaaarrrrgh' ... 'zz' 'zzs' 'zzx']
No. Of tokens:  31749


# Combining the Text & Subject vector matrix into single matrix

In [30]:
combined_vectors = hstack([subject_vectors,text_vectors])

In [31]:
print('Subject vectors:', subject_vectors.shape[1], '\nText vectors:', text_vectors.shape[1],'\nTotal:',text_vectors.shape[1]+subject_vectors.shape[1])

Subject vectors: 2971 
Text vectors: 31749 
Total: 34720


In [32]:
combined_vectors.toarray().shape

(2000, 34720)

## Vectorizing the concatenated text-subject string

In [54]:
concat_sub_text_vectors = tfidf_vectorizer.fit_transform(concatenated_sub_text)
print('Concatenated Subject Text Vectors: \n',concat_sub_text_vectors.toarray())
print('Tokens: ', tfidf_vectorizer.get_feature_names_out())
print('No. of Tokens: ', len(tfidf_vectorizer.get_feature_names_out()))

Concatenated Subject Text Vectors: 
 [[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]
Tokens:  ['aa' 'aaa' 'aaaaarrrrgh' ... 'zz' 'zzs' 'zzx']
No. of Tokens:  32005


# Train-Test Split

## Subject Train Test Split

In [33]:
X_subject = subject_vectors
y = blogs['Labels']

In [34]:
X_subject_train, X_subject_test, y_subject_train, y_subject_test = train_test_split(X_subject, y, test_size=0.2, random_state=42)

## Text train test split

In [35]:
X_text = text_vectors
y = blogs['Labels']

In [36]:
X_text_train, X_text_test, y_text_train, y_text_test = train_test_split(X_text, y, test_size=0.2, random_state=42)

## Text-Subject combined train test split

In [37]:
X_combined = combined_vectors.toarray()
y = blogs['Labels']

In [38]:
X_combined_train, X_combined_test, y_combined_train, y_combined_test = train_test_split(X_combined, y, test_size=0.2, random_state=42)

## Concatenated Text-Subject train test split

In [56]:
X_concat_train, X_concat_test, y_concat_train, y_concat_test = train_test_split(concat_sub_text_vectors, y, test_size=0.2, random_state=42)

# MultinomialNB classifier

## MultinomialNB on subject vectors

In [39]:
nb_classifier = MultinomialNB()

In [40]:
nb_classifier.fit(X_subject_train, y_subject_train) 

MultinomialNB()

In [41]:
y_subject_pred =  nb_classifier.predict(X_subject_test)

In [42]:
accuracy_score(y_subject_test, y_subject_pred)

0.5925

## MultinimialNB on text vectors

In [43]:
nb_classifier.fit(X_text_train, y_text_train) 

MultinomialNB()

In [44]:
y_text_pred =  nb_classifier.predict(X_text_test)

In [45]:
accuracy_score(y_text_test, y_text_pred)

0.6725

## MultinomialNB on Text-Subject Combined Vectors

In [46]:
nb_classifier.fit(X_combined_train, y_combined_train)

MultinomialNB()

In [47]:
y_combined_pred = nb_classifier.predict(X_combined_test)

In [48]:
accuracy_score(y_combined_test, y_combined_pred)

0.7825

## MultinomialNB on Concatenated Text-subject vectors

In [59]:
nb_classifier.fit(X_concat_train, y_concat_train)

MultinomialNB()

In [62]:
y_concat_pred = nb_classifier.predict(X_concat_test)

In [63]:
accuracy_score(y_concat_test, y_concat_pred)

0.755

# By taking Blog Text and Subject together, we are getting 75%+ accuracy 

# So we decide to move forward considering Text & Subject together, as our feature

# *********************************************************************************

# Tuning on parameters of TF-IDF & MultinomialNB

In [145]:
# Defining a pipeline consisting vectorization and classifier
pipeline = Pipeline([
    ('tfidf', TfidfVectorizer()),
    ('classifier', MultinomialNB())
])

#Defining the values of the parameters
param_grid = {
    'tfidf__max_df': [0.75, 0.85, 1.0],  # maximum document frequency
    'tfidf__min_df': [1,2,5],           # minimum document frequency
    'tfidf__ngram_range': [(1,1),(1,2)], # unigrams or bigrams
    'tfidf__use_idf': [True, False],     # use idf or not
    'tfidf__smooth_idf': [True, False],  # smooth IDF
    'tfidf__max_features': [10000, 20000, 30000, 40000],
    'classifier__alpha':[0.01, 0.1, 2, 3, 5, 10, 100]
    
}

In [146]:
# Creating instance of GridSearchCV
grid_search = GridSearchCV(pipeline, param_grid, cv=5, scoring='accuracy', n_jobs=-1)

In [147]:
# Performing the grid search on our dataset in which we have joint the subject and text of blogs to create single text document
grid_search.fit(concatenated_sub_text,y)


GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('tfidf', TfidfVectorizer()),
                                       ('classifier', MultinomialNB())]),
             n_jobs=-1,
             param_grid={'classifier__alpha': [0.01, 0.1, 2, 3, 5, 10, 100],
                         'tfidf__max_df': [0.75, 0.85, 1.0],
                         'tfidf__max_features': [10000, 20000, 30000, 40000],
                         'tfidf__min_df': [1, 2, 5],
                         'tfidf__ngram_range': [(1, 1), (1, 2)],
                         'tfidf__smooth_idf': [True, False],
                         'tfidf__use_idf': [True, False]},
             scoring='accuracy')

In [148]:

#Best results of grid search
print(grid_search.best_score_)
print(grid_search.best_params_)

gridsearch_results_dataframe = pd.DataFrame(grid_search.cv_results_)

0.78
{'classifier__alpha': 0.1, 'tfidf__max_df': 0.75, 'tfidf__max_features': 20000, 'tfidf__min_df': 1, 'tfidf__ngram_range': (1, 2), 'tfidf__smooth_idf': True, 'tfidf__use_idf': True}


<IPython.core.display.Javascript object>

## 78% is the best accuracy & the above parameters values are best as per the grid search results

# Let's use these parameter values for training and prediction

# On Concatenated Subject & Text dataset

In [256]:
# Defining a pipeline consisting vectorization and classifier
pipeline = Pipeline([
    ('tfidf', TfidfVectorizer(max_df= 0.75, max_features= 20000, min_df = 1, ngram_range = (1, 2), smooth_idf= True, use_idf= True)),
    ('classifier', MultinomialNB(alpha=0.1))
])

In [257]:
# Getting the cross validated accuracy
cross_val_scores = cross_val_score(pipeline, X=concatenated_sub_text, y=y, cv=5, scoring='accuracy', n_jobs=-1)
cross_val_scores.mean()

0.78

## The cross validated accuracy is 78%

# On separately vectorizing Text and Subject then merging into a single vector matrix

In [258]:
# Defining thr TF-IDF vectorizer with the best parameters
tfidf = TfidfVectorizer(max_df= 0.75, max_features= 20000, min_df = 1, ngram_range = (1, 2), smooth_idf= True, use_idf= True)

In [259]:
# Vectorizing the blog text
text_vectors = tfidf.fit_transform(text)

In [260]:
#Vectorizing the Blog subject
subject_vectors = tfidf.fit_transform(subject)

In [261]:
# Combining the two matrix obtained above into a single vector matrix
combined_vectors = hstack([subject_vectors,text_vectors])
print('Subject vectors:', subject_vectors.shape[1], '\nText vectors:', text_vectors.shape[1],'\nTotal:',text_vectors.shape[1]+subject_vectors.shape[1])

Subject vectors: 6665 
Text vectors: 20000 
Total: 26665


In [262]:
nb_classifier = MultinomialNB(alpha=0.1)

In [263]:
cross_val_scores = cross_val_score(nb_classifier, X=combined_vectors, y=y, cv=5, scoring='accuracy', n_jobs=-1)
cross_val_scores.mean()

0.7969999999999999

## The cross validated accuracy is 79.6%

# Sentiment Analysis

In [2]:
from transformers import AutoTokenizer, AutoModelForSequenceClassification


In [23]:
model = AutoModelForSequenceClassification.from_pretrained(r"d:\ExcelR\Model_and_Tokenizer\cardiffnlp\twitter-roberta-base-sentiment")
tokenizer = AutoTokenizer.from_pretrained(r"d:\ExcelR\Model_and_Tokenizer\cardiffnlp\twitter-roberta-base-sentiment")

D:\Program Files\Anaconda\Lib\site-packages\transformers\modeling_utils.py:479: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(checkpoint_file, map_location

In [26]:
example = ["u are a good person. I like your company", "The taste is not as it was used to"]
token_ids = tokenizer(example, return_tensors='pt',  padding=True)
example_input_ids = token_ids['input_ids']
example_attn_masks = token_ids['attention_mask']

In [28]:
example_model_output = model(example_input_ids, example_attn_masks )
example_model_output

SequenceClassifierOutput(loss=None, logits=tensor([[-2.5715, -0.3296,  3.6114],
        [ 2.0110,  0.3631, -2.6152]], grad_fn=<AddmmBackward0>), hidden_states=None, attentions=None)

In [29]:
example_model_output = model(input_ids = example_input_ids, attention_mask = example_attn_masks )
example_model_output

SequenceClassifierOutput(loss=None, logits=tensor([[-2.5715, -0.3296,  3.6114],
        [ 2.0110,  0.3631, -2.6152]], grad_fn=<AddmmBackward0>), hidden_states=None, attentions=None)

In [41]:
labels = ['Negative', 'Neutral', 'Positive']
probs = torch.nn.functional.softmax(example_model_output.logits[0], dim=-1)
predicted_class = torch.argmax(probs, dim=-1).item()
print(labels[predicted_class], probs.tolist())

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Positive [0.002021094085648656, 0.01902080699801445, 0.9789581298828125]


In [26]:
#Tokenizing the blog text using tokenizer of our model
tokened_data = tokenizer(data['text'].to_list(), return_tensors='pt',  padding=True)


In [27]:
tokened_data

{'input_ids': tensor([[    0,  3654,   154,  ...,     1,     1,     1],
        [    0, 37111, 36122,  ...,     1,     1,     1],
        [    0,   642,   579,  ...,     1,     1,     1],
        ...,
        [    0,   118,    40,  ...,     1,     1,     1],
        [    0, 28481,   658,  ...,     1,     1,     1],
        [    0, 28481,   658,  ...,     1,     1,     1]]), 'attention_mask': tensor([[1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0],
        ...,
        [1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0]])}

In [130]:
#Our Text data is converted into a sequence of 11255 tokens
len(tokened_data['input_ids'][9])

11255

# The model can only perform sentiment analysis on sequence of upto 512 tokens
# We will need to create chunks of our token sequences. each sequence being 512 tokens long

In [46]:
def sentiment_analysis_on_chunks(text):
        try:
            tokened_input = tokenizer(text, return_tensors="pt")

            token_input_ids = tokened_input['input_ids'][0]
            token_attn_mask = tokened_input['attention_mask'][0]
            
            id_chunks = [token_input_ids[i:i+511] for i in range(0, len(token_input_ids), 511)]
            
            mask_chunks = [token_attn_mask[i:i+511] for i in range(0, len(token_attn_mask), 511)]
            
            sentiment_labels = ["Negative","Neutral","Positive"]
            positive_scores = []
            negative_scores = []
            neutral_scores = []
            

            for ids, mask in zip(id_chunks, mask_chunks):
                ids = torch.stack([ids])
                mask = torch.stack([mask])
                with torch.no_grad():
                    model_output =  model(input_ids = ids, attention_mask = mask)
                sentiment_scores = model_output.logits
                sentiment_prob = torch.nn.functional.softmax(sentiment_scores, dim=1)[0]
            
                negative_scores.append(sentiment_prob[0]*len(ids[0]))
                neutral_scores.append(sentiment_prob[1]*len(ids[0]))
                positive_scores.append(sentiment_prob[2]*len(ids[0]))
            
            neg_prob = sum(negative_scores)/len(token_input_ids)
            neu_prob = sum(neutral_scores)/len(token_input_ids)
            pos_prob = sum(positive_scores)/len(token_input_ids)
            sentiment_prob = torch.stack([neg_prob, neu_prob, pos_prob])
            sentiment_prob = torch.stack([sentiment_prob])

            sentiment_index = torch.argmax(sentiment_prob, dim=1)
            
            sentiment = sentiment_labels[sentiment_index]
            return sentiment_prob, sentiment
        
        except RuntimeError:
                pass

In [47]:
sentiment_analysis_on_chunks(data.text[0])

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

(tensor([[0.5539, 0.4180, 0.0281]]), 'Negative')

In [48]:
data

subject  \
0                                      islamic genocide   
1                                          not the omni   
2                       yet more rushdie re islamic law   
3                           death penalty gulf war long   
4                           rawlins debunks creationism   
...                                                 ...   
1995  after years can we say that christian morality is   
1996                       who is next mormons and jews   
1997               the gospels josephus etc and origins   
1998                         catholic lit crit of a s s   
1999                       who is next mormons and jews   

                                                   text  
0     noting that a particular society in this case ...  
1     please enlighten me how is omnipotence contrad...  
2     p s i am not sure about this but i think the c...  
3     which liberal news media are we talking about ...  
4     evolution as i have said before is theory and ...  
...                                                 ...  
1995  presumably this means that some moral systems ...  
1996  the fbi claims on the basis of their intellige...  
1997  i will agree that creation should not be taugh...  
1998  followup to talk religion misc alt sex stories...  
1999  followup to sci skeptic talk politics misc tal...  

[2000 rows x 2 columns]

In [49]:
data[['Negative','Neutral', 'Positive','Sentiment' ]] = [{},{},{},{}]
data

subject  \
0                                      islamic genocide   
1                                          not the omni   
2                       yet more rushdie re islamic law   
3                           death penalty gulf war long   
4                           rawlins debunks creationism   
...                                                 ...   
1995  after years can we say that christian morality is   
1996                       who is next mormons and jews   
1997               the gospels josephus etc and origins   
1998                         catholic lit crit of a s s   
1999                       who is next mormons and jews   

                                                   text Negative Neutral  \
0     noting that a particular society in this case ...      NaN     NaN   
1     please enlighten me how is omnipotence contrad...      NaN     NaN   
2     p s i am not sure about this but i think the c...      NaN     NaN   
3     which liberal news media are we talking about ...      NaN     NaN   
4     evolution as i have said before is theory and ...      NaN     NaN   
...                                                 ...      ...     ...   
1995  presumably this means that some moral systems ...      NaN     NaN   
1996  the fbi claims on the basis of their intellige...      NaN     NaN   
1997  i will agree that creation should not be taugh...      NaN     NaN   
1998  followup to talk religion misc alt sex stories...      NaN     NaN   
1999  followup to sci skeptic talk politics misc tal...      NaN     NaN   

     Positive Sentiment  
0         NaN       NaN  
1         NaN       NaN  
2         NaN       NaN  
3         NaN       NaN  
4         NaN       NaN  
...       ...       ...  
1995      NaN       NaN  
1996      NaN       NaN  
1997      NaN       NaN  
1998      NaN       NaN  
1999      NaN       NaN  

[2000 rows x 6 columns]

In [50]:
for text, i in zip(data['text'], data.index):
    sentiment_score_tensor, blog_sentiment = sentiment_analysis_on_chunks(text)
    data.loc[i, 'Negative'] = sentiment_score_tensor[0][0]
    data.loc[i, 'Neutral'] = sentiment_score_tensor[0][1]
    data.loc[i, 'Positive'] = sentiment_score_tensor[0][2]
    data.loc[i, 'Sentiments'] = blog_sentiment

data

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

subject  \
0                                      islamic genocide   
1                                          not the omni   
2                       yet more rushdie re islamic law   
3                           death penalty gulf war long   
4                           rawlins debunks creationism   
...                                                 ...   
1995  after years can we say that christian morality is   
1996                       who is next mormons and jews   
1997               the gospels josephus etc and origins   
1998                         catholic lit crit of a s s   
1999                       who is next mormons and jews   

                                                   text        Negative  \
0     noting that a particular society in this case ...  tensor(0.5539)   
1     please enlighten me how is omnipotence contrad...  tensor(0.3070)   
2     p s i am not sure about this but i think the c...  tensor(0.5710)   
3     which liberal news media are we talking about ...  tensor(0.6843)   
4     evolution as i have said before is theory and ...  tensor(0.3151)   
...                                                 ...             ...   
1995  presumably this means that some moral systems ...  tensor(0.3226)   
1996  the fbi claims on the basis of their intellige...  tensor(0.2933)   
1997  i will agree that creation should not be taugh...  tensor(0.0805)   
1998  followup to talk religion misc alt sex stories...  tensor(0.2959)   
1999  followup to sci skeptic talk politics misc tal...  tensor(0.3734)   

             Neutral        Positive Sentiment Sentiments  
0     tensor(0.4180)  tensor(0.0281)       NaN   Negative  
1     tensor(0.6383)  tensor(0.0548)       NaN    Neutral  
2     tensor(0.3987)  tensor(0.0303)       NaN   Negative  
3     tensor(0.2859)  tensor(0.0298)       NaN   Negative  
4     tensor(0.5685)  tensor(0.1164)       NaN    Neutral  
...              ...             ...       ...        ...  
1995  tensor(0.5896)  tensor(0.0878)       NaN    Neutral  
1996  tensor(0.6247)  tensor(0.0820)       NaN    Neutral  
1997  tensor(0.7476)  tensor(0.1718)       NaN    Neutral  
1998  tensor(0.5428)  tensor(0.1613)       NaN    Neutral  
1999  tensor(0.5659)  tensor(0.0608)       NaN    Neutral  

[2000 rows x 7 columns]

In [ ]:
data.to_pickle('sentiment_analysis')